In [1]:
import torch
from torch import nn
import numpy as np
import os
import time
import codecs
import re
import json
import pandas as pd
import glob
import datetime
import random

In [2]:
#GET FAT AND WEIGHT DATA

#things to fill out
rootdir = "GavneetSabharwal/Personal & Account"
regex = re.compile('weight-2021-03-04')
startDate = '03/08/21' 
endDate = '03/28/21'

#get time period
startd = datetime.datetime.strptime(startDate, "%m/%d/%y")
endd = datetime.datetime.strptime(endDate, "%m/%d/%y")#

#gets range of dates between start and end
date_array = (startd + datetime.timedelta(days=x) for x in range(0, (endd-startd).days))
dates = []
for date_object in date_array:
    #gets date value as string
    dates = np.append(dates, date_object.strftime("%m/%d/%y"))

    
#get weight files
filenames = os.listdir(rootdir)
weights= []
for root, dirs, files in os.walk(rootdir):
    for file in files:
        if regex.match(file):
            weights = np.append(weights, file)
print(weights)            


#get weight data
roughdata = []
for x in range(np.size(weights)):
    filename = rootdir + "/" + weights[x]    
    data = []
    weight = []
    fat = []
    with open(filename) as json_file:
        rawdata = json.load(json_file)
        
        #checks if data is within start and end date
        for n in range(np.size(rawdata)):
            date = rawdata[n]["date"]
            if date in dates:
                roughdata.append(rawdata[n])  
                
        #delete irrelevant information then save relevant info
        for x in range(np.size(roughdata)):    
            del roughdata[x]["logId"]
            del roughdata[x]["time"]
            del roughdata[x]["source"]
            del roughdata[x]["bmi"]
            weight = np.append(weight, roughdata[x]["weight"])
            fat = np.append(fat, roughdata[x]["fat"])

        data = np.append(data, roughdata)

print(fat)
print(weight)

['weight-2021-03-04.json']
[25.6 25.  24.7 24.7 24.2 24.2 24.3 24.5 25.  24.5 24.  23.6 24.1 24.
 23.8 23.7 23.8 23.6 23.2 23. ]
[135.2 134.4 134.2 134.2 133.4 133.4 133.6 133.8 134.2 133.4 132.8 132.3
 133.1 132.8 132.6 132.3 132.4 132.2 131.9 131.8]


In [3]:
#GET CALORIE DATA

#things to fill out
rootdir = "GavneetSabharwal/Nutrition"
regex = re.compile('food_logs-0||food_logs-100')
startD = "2021-03-07"
endD = "2021-03-27"

#get calorie files
filenames = os.listdir(rootdir)
foodfiles = []
for root, dirs, files in os.walk(rootdir):
    for file in files:
        if regex.match(file):
            foodfiles = np.append(foodfiles, file)


#start boolean for when data is within date range
start = False



data = []
#get food entries
for x in range(np.size(foodfiles)):
    filename = rootdir + "/" + foodfiles[x]
    count = 0
    
    with open(filename) as json_file:
        roughdata = json.load(json_file)
     
        for y in range(np.size(roughdata)):
            
            #start reading data within date range
            if roughdata[y-count]["logDate"] == startD:
                start = False
            if roughdata[y-count]["logDate"] == endD:
                start = True
                
            #once within date range:
            if start == True:
                #delete irrelevant informaiton and track calorie information
                cal = roughdata[y-count]["loggedFood"]["calories"]                
                del roughdata[y-count]["logId"]
                del roughdata[y-count]["loggedFood"]
                del roughdata[y-count]["favorite"]
                #if the data contains extra nutritionalvalues data slot, delete that also
                if "nutritionalValues" in roughdata[y-count].keys():                
                    del roughdata[y-count]["nutritionalValues"]                
                roughdata[y-count]["calories"] = cal
            else:
                #delete data outside of date range
                del roughdata[y-count]
                count +=1
        data = np.append(data, roughdata) 
#get calories for each day
calories = data[0]["calories"]
totCalories = np.empty((0,1))
dates = np.empty((0,1))

count = 0
for x in range(1, len(data)):
    
    #if next food entry is from the same date
    if data[x-1]["logDate"] == data[x]["logDate"]:
        
        #add to calorie counter for the day
        calories += data[x]["calories"]
        
        #add to list of calories per day if at end of loop
        if x == len(data)-1:
            totCalories = np.vstack((totCalories, calories))
    #add to list of calories per day if new day
    else:
        dates = np.vstack((dates, data[x-1]["logDate"]))
        totCalories = np.vstack((totCalories, calories))
        calories = data[x]["calories"]
    
totCalories = np.flip(totCalories)
print(totCalories)


[[1591.]
 [1599.]
 [1595.]
 [1540.]
 [1674.]
 [1557.]
 [1599.]
 [1881.]
 [1346.]
 [1465.]
 [1456.]
 [2197.]
 [1562.]
 [1555.]
 [1582.]
 [1613.]
 [1504.]
 [1473.]
 [1548.]
 [1843.]]


In [4]:
#GET RELATIVE CALORIE DATA

#calculate calories burned more/less than consumed based on weight change
def caloriesBurned(weight, fat):
    fatMass = []
    leanMass = []
    for x in range(len(weight)):
        fatMass = np.append(fatMass, weight[x]*fat[x]/100)
        leanMass = np.append(leanMass, weight[x] - fatMass[x])
    calories = [] 
    for x in range(len(weight) - 1):   
        calories = np.append(calories, -(fatMass[x]-fatMass[x+1])*442.39)
        if leanMass[x] >= leanMass[x+1]:
            calories[x] -= (leanMass[x] - leanMass[x+1])*70
        else:
            calories[x] -= (leanMass[x]-leanMass[x+1])*265
    calories = np.append(calories, [0])

    return calories
        
#calculate total calories burned in a day
calories = caloriesBurned(weight, fat)
print(calories)
for x in range(len(calories)):
    calories[x] = totCalories[x] - calories[x]

#calories = np.append(calories, [2000,2000, 2000])
print(calories)

[-391.376768 -133.286714   -0.       -365.371394   -0.         85.28498
  131.749718  314.36791  -365.79713  -302.86329  -247.661588  374.132777
  -97.377189 -108.558548  -96.855843   65.130079 -108.34568  -185.650176
  -77.375452    0.      ]
[1982.376768 1732.286714 1595.       1905.371394 1674.       1471.71502
 1467.250282 1566.63209  1711.79713  1767.86329  1703.661588 1822.867223
 1659.377189 1663.558548 1678.855843 1547.869921 1612.34568  1658.650176
 1625.375452 1843.      ]


In [ ]:
#things to fill in
rootdir = "GavneetSabharwal/Physical Activity"
regex = re.compile('heart_rate-2021-03-([0][8-9]|[1][0-9]|[2][0-7])')
#get heart rates

filenames = os.listdir(rootdir)
heartRates = []
for root, dirs, files in os.walk(rootdir):
    for file in files:
        if regex.match(file):
            heartRates = np.append(heartRates, file)

#read files for hr data
inputs = np.empty((0,3))
newInput = np.empty(3)
dateTime = []
start = False
minInputs = np.empty((0,3))
hrDates = np.empty((0,1))

date = startDate
inputs = np.empty((0, 3))
tempInputs = np.empty((0, 3))
count = 0


#read heart rate data files
for x in range(np.size(heartRates)):
    filename = rootdir + "/" + heartRates[x]
    data = []
    with open(filename) as json_file:
        data = json.load(json_file)
        tempInputs = np.empty((len(data), 3))
        
        #get inputs from heart rate files
        for y in range(len(data)):  
            #get time of data recording
            temp = data[y]["dateTime"][9:] 
            #convert time input to seconds through the day
            tempInputs[y][0] = int(temp[:2])*3600  + int(temp[3:5])*60 + int(temp[6:9])
            tempInputs[y][1] = int(data[y]["value"]["bpm"])
            #set third input to day of recording
            tempInputs[y][2] = x
        if x == 0:
            inputs = tempInputs
        else:
            #add data recording to list of data records
            inputs = np.vstack((inputs, tempInputs))

            
for x in range(len(inputs)-1):
    inputs[x+1][0] = inputs[x+1][0] -inputs[x][0]
        

for x in range(len(inputs)):
    if inputs[x][1] > 10:
        print(inputs[x])
    #    inputs = np.insert(inputs, x+1, [inputs[x][0], inputs[x][1]-10, inputs[x][2]], axis=0)
    #    inputs[x][1] = 10
        
'''for x in range(5):
    condensedInputs =[]
    for y in range(1, len(inputs), 2):    
        if inputs[y][2] == inputs[y-1][2]:
            groupInput = inputs[y] + inputs[y-1]
            groupInput[1] = groupInput[1]/2
            groupInput[2] = groupInput[2]/2
            condensedInputs.append(groupInput)
    inputs = condensedInputs
'''
day = 0
splitInputs = []
lastSplit = 0
for x in range(len(inputs)):
    if inputs[x][2] != day:
        splitInputs.append(x - lastSplit)
        lastSplit = x
        day +=1

splitInputs.append(len(inputs) - lastSplit)
        
        


from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler(feature_range=(-1,1))
for x in range(len(inputs)):
    if x < len(inputs)-1:
        inputs[x][0] = inputs[x+1][0] - inputs[x][0]
inputs = np.delete(inputs, len(inputs)-1, 0)
splitInputs[len(splitInputs)-1] -=1



#normalize, scale and format

train_data_normalized2 = scaler.fit_transform(np.transpose(inputs)[1] .reshape(-1,1))
scaler = MinMaxScaler(feature_range=(-1,1))

train_data_normalized1 = scaler.fit_transform(np.transpose(inputs)[0] .reshape(-1,1))

scaler = MinMaxScaler(feature_range=(-1,1))

#train_data_normalized3 = scaler.fit_transform(np.transpose(inputs)[2] .reshape(-1,1))

train_data_normalized = np.hstack((train_data_normalized1, train_data_normalized2))

#train_data_normalized = np.hstack((train_data_normalized, train_data_normalized3))


inputs = torch.FloatTensor(train_data_normalized)
numOfInputs = np.size(np.transpose(inputs)[0])
print(np.shape(inputs))
print(inputs)

[ 3. 78.  0.]
[ 5. 79.  0.]
[ 8. 80.  0.]
[20. 79.  0.]
[13. 78.  0.]
[25. 76.  0.]
[18. 75.  0.]
[30. 74.  0.]
[23. 72.  0.]
[45. 71.  0.]
[28. 73.  0.]
[60. 72.  0.]
[38. 73.  0.]
[75. 74.  0.]
[43. 73.  0.]
[85. 74.  0.]
[48. 73.  0.]
[90. 74.  0.]
[53. 73.  0.]
[105.  71.   0.]
[63. 70.  0.]
[120.  69.   0.]
[73. 72.  0.]
[125.  74.   0.]
[78. 75.  0.]
[135.  74.   0.]
[83. 72.  0.]
[140.  71.   0.]
[88. 69.  0.]
[145.  70.   0.]
[93. 72.  0.]
[150.  78.   0.]
[98. 81.  0.]
[160.  80.   0.]
[113.  78.   0.]
[165.  75.   0.]
[118.  74.   0.]
[170.  73.   0.]
[123.  71.   0.]
[175.  70.   0.]
[128.  69.   0.]
[180.  70.   0.]
[133.  69.   0.]
[185.  70.   0.]
[138.  64.   0.]
[190.  66.   0.]
[143.  67.   0.]
[195.  69.   0.]
[153.  70.   0.]
[205.  69.   0.]
[158.  68.   0.]
[215.  70.   0.]
[163.  72.   0.]
[220.  71.   0.]
[168.  68.   0.]
[225.  67.   0.]
[173.  65.   0.]
[235.  66.   0.]
[188.  66.   0.]
[240.  67.   0.]
[193.  68.   0.]
[245.  69.   0.]
[198.  70.   0.]
[260.  

[2155.   56.    0.]
[2291.   54.    0.]
[2160.   58.    0.]
[2296.   56.    0.]
[2170.   57.    0.]
[2301.   59.    0.]
[2175.   60.    0.]
[2306.   59.    0.]
[2185.   61.    0.]
[2311.   63.    0.]
[2190.   64.    0.]
[2326.   64.    0.]
[2195.   61.    0.]
[2333.   58.    0.]
[2200.   59.    0.]
[2348.   60.    0.]
[2205.   59.    0.]
[2353.   59.    0.]
[2210.   65.    0.]
[2358.   65.    0.]
[2215.   66.    0.]
[2363.   67.    0.]
[2220.   66.    0.]
[2378.   66.    0.]
[2225.   65.    0.]
[2383.   64.    0.]
[2235.   65.    0.]
[2388.   66.    0.]
[2240.   65.    0.]
[2398.   66.    0.]
[2245.   65.    0.]
[2403.   63.    0.]
[2255.   62.    0.]
[2413.   63.    0.]
[2260.   64.    0.]
[2418.   63.    0.]
[2265.   62.    0.]
[2423.   58.    0.]
[2270.   58.    0.]
[2428.   58.    0.]
[2275.   59.    0.]
[2433.   58.    0.]
[2280.   56.    0.]
[2438.   58.    0.]
[2285.   62.    0.]
[2443.   63.    0.]
[2290.   64.    0.]
[2448.   60.    0.]
[2300.   61.    0.]
[2453.   63.    0.]


[3736.   60.    0.]
[3972.   61.    0.]
[3741.   62.    0.]
[3977.   61.    0.]
[3746.   60.    0.]
[3982.   57.    0.]
[3756.   61.    0.]
[3987.   64.    0.]
[3761.   63.    0.]
[3997.   64.    0.]
[3766.   65.    0.]
[4002.   66.    0.]
[3771.   65.    0.]
[4007.   62.    0.]
[3776.   60.    0.]
[4012.   59.    0.]
[3786.   62.    0.]
[4017.   63.    0.]
[3801.   64.    0.]
[4022.   65.    0.]
[3806.   68.    0.]
[4027.   69.    0.]
[3811.   70.    0.]
[4037.   67.    0.]
[3816.   66.    0.]
[4042.   65.    0.]
[3821.   65.    0.]
[4047.   64.    0.]
[3826.   61.    0.]
[4052.   58.    0.]
[3831.   60.    0.]
[4057.   63.    0.]
[3836.   61.    0.]
[4062.   60.    0.]
[3841.   63.    0.]
[4067.   63.    0.]
[3846.   65.    0.]
[4072.   67.    0.]
[3851.   68.    0.]
[4077.   66.    0.]
[3856.   65.    0.]
[4082.   63.    0.]
[3861.   62.    0.]
[4092.   63.    0.]
[3871.   64.    0.]
[4097.   65.    0.]
[3876.   64.    0.]
[4102.   63.    0.]
[3881.   64.    0.]
[4112.   63.    0.]


[5072.   79.    0.]
[5379.   84.    0.]
[5077.   80.    0.]
[5384.   74.    0.]
[5082.   64.    0.]
[5389.   59.    0.]
[5087.   57.    0.]
[5394.   56.    0.]
[5092.   55.    0.]
[5399.   53.    0.]
[5102.   57.    0.]
[5404.   60.    0.]
[5112.   59.    0.]
[5409.   58.    0.]
[5117.   55.    0.]
[5414.   57.    0.]
[5122.   59.    0.]
[5424.   60.    0.]
[5132.   62.    0.]
[5434.   61.    0.]
[5137.   60.    0.]
[5439.   58.    0.]
[5142.   59.    0.]
[5444.   61.    0.]
[5152.   64.    0.]
[5449.   63.    0.]
[5157.   59.    0.]
[5459.   60.    0.]
[5162.   61.    0.]
[5464.   63.    0.]
[5167.   64.    0.]
[5479.   64.    0.]
[5172.   65.    0.]
[5494.   64.    0.]
[5177.   65.    0.]
[5499.   66.    0.]
[5182.   64.    0.]
[5514.   64.    0.]
[5187.   65.    0.]
[5524.   62.    0.]
[5192.   61.    0.]
[5529.   62.    0.]
[5197.   64.    0.]
[5534.   66.    0.]
[5202.   65.    0.]
[5539.   64.    0.]
[5207.   63.    0.]
[5549.   64.    0.]
[5217.   63.    0.]
[5554.   62.    0.]


[7007.   61.    0.]
[7115.   60.    0.]
[7017.   61.    0.]
[7120.   65.    0.]
[7022.   64.    0.]
[7125.   62.    0.]
[7032.   62.    0.]
[7130.   63.    0.]
[7042.   64.    0.]
[7135.   69.    0.]
[7047.   74.    0.]
[7140.   75.    0.]
[7052.   68.    0.]
[7145.   64.    0.]
[7057.   57.    0.]
[7150.   55.    0.]
[7072.   55.    0.]
[7155.   55.    0.]
[7087.   56.    0.]
[7165.   59.    0.]
[7092.   56.    0.]
[7170.   57.    0.]
[7102.   58.    0.]
[7180.   57.    0.]
[7107.   56.    0.]
[7190.   57.    0.]
[7112.   56.    0.]
[7195.   55.    0.]
[7122.   56.    0.]
[7210.   55.    0.]
[7127.   55.    0.]
[7215.   56.    0.]
[7132.   55.    0.]
[7220.   56.    0.]
[7137.   58.    0.]
[7225.   60.    0.]
[7142.   59.    0.]
[7230.   58.    0.]
[7152.   57.    0.]
[7240.   58.    0.]
[7157.   57.    0.]
[7245.   55.    0.]
[7162.   54.    0.]
[7260.   54.    0.]
[7167.   55.    0.]
[7265.   56.    0.]
[7177.   55.    0.]
[7280.   55.    0.]
[7192.   56.    0.]
[7285.   56.    0.]


...

[-1.41304e+05  9.80000e+01  1.00000e+01]
[2.05688e+05 9.70000e+01 1.00000e+01]
[-1.41299e+05  9.60000e+01  1.00000e+01]
[2.05693e+05 9.40000e+01 1.00000e+01]
[-1.41294e+05  9.10000e+01  1.00000e+01]
[2.05703e+05 9.00000e+01 1.00000e+01]
[-1.41284e+05  8.90000e+01  1.00000e+01]
[2.05708e+05 8.70000e+01 1.00000e+01]
[-1.41279e+05  8.60000e+01  1.00000e+01]
[2.05718e+05 8.40000e+01 1.00000e+01]
[-1.41274e+05  8.50000e+01  1.00000e+01]
[2.05723e+05 7.80000e+01 1.00000e+01]
[-1.41269e+05  7.70000e+01  1.00000e+01]
[2.05733e+05 7.60000e+01 1.00000e+01]
[-1.41264e+05  7.70000e+01  1.00000e+01]
[2.05738e+05 7.50000e+01 1.00000e+01]
[-1.41259e+05  7.00000e+01  1.00000e+01]
[2.05743e+05 6.70000e+01 1.00000e+01]
[-1.41249e+05  6.60000e+01  1.00000e+01]
[2.05748e+05 6.70000e+01 1.00000e+01]
[-1.41244e+05  6.80000e+01  1.00000e+01]
[2.05753e+05 7.00000e+01 1.00000e+01]
[-1.41239e+05  7.10000e+01  1.00000e+01]
[2.05758e+05 7.20000e+01 1.00000e+01]
[-1.41234e+05  7.00000e+01  1.00000e+01]
[2.05763e+0

[2.07169e+05 5.40000e+01 1.00000e+01]
[-1.39869e+05  5.20000e+01  1.00000e+01]
[2.07174e+05 5.20000e+01 1.00000e+01]
[-1.39864e+05  5.30000e+01  1.00000e+01]
[2.07179e+05 5.20000e+01 1.00000e+01]
[-1.39859e+05  5.20000e+01  1.00000e+01]
[2.07194e+05 5.40000e+01 1.00000e+01]
[-1.39849e+05  5.50000e+01  1.00000e+01]
[2.07199e+05 5.60000e+01 1.00000e+01]
[-1.39844e+05  5.90000e+01  1.00000e+01]
[2.07204e+05 5.60000e+01 1.00000e+01]
[-1.39839e+05  5.40000e+01  1.00000e+01]
[2.07209e+05 5.40000e+01 1.00000e+01]
[-1.39834e+05  5.30000e+01  1.00000e+01]
[2.07214e+05 5.20000e+01 1.00000e+01]
[-1.39829e+05  5.20000e+01  1.00000e+01]
[2.07224e+05 5.20000e+01 1.00000e+01]
[-1.39824e+05  5.30000e+01  1.00000e+01]
[2.07229e+05 5.30000e+01 1.00000e+01]
[-1.39814e+05  5.40000e+01  1.00000e+01]
[2.07234e+05 5.50000e+01 1.00000e+01]
[-1.39804e+05  5.60000e+01  1.00000e+01]
[2.07249e+05 5.60000e+01 1.00000e+01]
[-1.39799e+05  5.50000e+01  1.00000e+01]
[2.07254e+05 5.40000e+01 1.00000e+01]
[-1.39789e+05 

[2.08692e+05 5.50000e+01 1.00000e+01]
[-1.2747e+05  5.4000e+01  1.0000e+01]
[2.08697e+05 5.20000e+01 1.00000e+01]
[-1.27465e+05  5.30000e+01  1.00000e+01]
[2.08712e+05 5.30000e+01 1.00000e+01]
[-1.2746e+05  5.2000e+01  1.0000e+01]
[2.08722e+05 5.10000e+01 1.00000e+01]
[-1.2745e+05  5.0000e+01  1.0000e+01]
[2.08727e+05 4.90000e+01 1.00000e+01]
[-1.2744e+05  4.8000e+01  1.0000e+01]
[2.08742e+05 4.80000e+01 1.00000e+01]
[-1.27425e+05  5.00000e+01  1.00000e+01]
[2.08747e+05 5.20000e+01 1.00000e+01]
[-1.2742e+05  5.3000e+01  1.0000e+01]
[2.08752e+05 5.40000e+01 1.00000e+01]
[-1.27415e+05  5.50000e+01  1.00000e+01]
[2.08762e+05 5.40000e+01 1.00000e+01]
[-1.2741e+05  5.2000e+01  1.0000e+01]
[2.08767e+05 5.00000e+01 1.00000e+01]
[-1.274e+05  5.000e+01  1.000e+01]
[2.08777e+05 4.90000e+01 1.00000e+01]
[-1.27385e+05  4.90000e+01  1.00000e+01]
[2.08782e+05 5.00000e+01 1.00000e+01]
[-1.2738e+05  4.9000e+01  1.0000e+01]
[2.08797e+05 4.80000e+01 1.00000e+01]
[-1.27375e+05  4.80000e+01  1.00000e+01]


[2.09866e+05 5.00000e+01 1.00000e+01]
[-1.26054e+05  5.20000e+01  1.00000e+01]
[2.09871e+05 4.90000e+01 1.00000e+01]
[-1.26039e+05  4.90000e+01  1.00000e+01]
[2.09886e+05 4.80000e+01 1.00000e+01]
[-1.26024e+05  4.80000e+01  1.00000e+01]
[2.09901e+05 4.90000e+01 1.00000e+01]
[-1.26009e+05  4.80000e+01  1.00000e+01]
[2.09916e+05 4.90000e+01 1.00000e+01]
[-1.25994e+05  5.00000e+01  1.00000e+01]
[2.09931e+05 4.90000e+01 1.00000e+01]
[-1.25979e+05  4.90000e+01  1.00000e+01]
[2.09946e+05 4.90000e+01 1.00000e+01]
[-1.25974e+05  4.90000e+01  1.00000e+01]
[2.09951e+05 5.00000e+01 1.00000e+01]
[-1.25959e+05  5.00000e+01  1.00000e+01]
[2.09956e+05 4.90000e+01 1.00000e+01]
[-1.25944e+05  4.90000e+01  1.00000e+01]
[2.09971e+05 5.00000e+01 1.00000e+01]
[-1.25929e+05  5.10000e+01  1.00000e+01]
[2.09976e+05 5.00000e+01 1.00000e+01]
[-1.25914e+05  5.00000e+01  1.00000e+01]
[2.09981e+05 4.90000e+01 1.00000e+01]
[-1.25904e+05  5.00000e+01  1.00000e+01]
[2.09996e+05 5.10000e+01 1.00000e+01]
[-1.25899e+05 

[2.10796e+05 5.00000e+01 1.00000e+01]
[-1.25192e+05  5.00000e+01  1.00000e+01]
[2.10801e+05 5.10000e+01 1.00000e+01]
[-1.25187e+05  5.00000e+01  1.00000e+01]
[2.10806e+05 4.90000e+01 1.00000e+01]
[-1.25172e+05  4.90000e+01  1.00000e+01]
[2.10821e+05 5.00000e+01 1.00000e+01]
[-1.25162e+05  5.00000e+01  1.00000e+01]
[2.10826e+05 4.80000e+01 1.00000e+01]
[-1.25147e+05  4.80000e+01  1.00000e+01]
[2.10831e+05 5.00000e+01 1.00000e+01]
[-1.25132e+05  5.00000e+01  1.00000e+01]
[2.10836e+05 5.10000e+01 1.00000e+01]
[-1.25122e+05  4.90000e+01  1.00000e+01]
[2.10846e+05 5.00000e+01 1.00000e+01]
[-1.25112e+05  5.10000e+01  1.00000e+01]
[2.10861e+05 5.10000e+01 1.00000e+01]
[-1.25106e+05  5.10000e+01  1.00000e+01]
[2.10876e+05 5.10000e+01 1.00000e+01]
[-1.25101e+05  5.00000e+01  1.00000e+01]
[2.10881e+05 4.90000e+01 1.00000e+01]
[-1.25086e+05  5.00000e+01  1.00000e+01]
[2.10896e+05 5.00000e+01 1.00000e+01]
[-1.25076e+05  5.10000e+01  1.00000e+01]
[2.10901e+05 5.00000e+01 1.00000e+01]
[-1.25061e+05 

In [50]:
#calculate expected outputs
y_actual = []
day = 0




scaler = MinMaxScaler(feature_range=(-1,1))
normalized_y = torch.FloatTensor(scaler.fit_transform(calories .reshape(-1,1)))
print(np.shape(normalized_y))

outputs = normalized_y
print(np.shape(outputs))
print(outputs)

torch.Size([20, 1])
torch.Size([20, 1])
tensor([[ 1.0000],
        [ 0.0290],
        [-0.5040],
        [ 0.7010],
        [-0.1973],
        [-0.9827],
        [-1.0000],
        [-0.6141],
        [-0.0505],
        [ 0.1671],
        [-0.0821],
        [ 0.3807],
        [-0.2541],
        [-0.2378],
        [-0.1784],
        [-0.6870],
        [-0.4367],
        [-0.2569],
        [-0.3861],
        [ 0.4589]])


In [8]:
class MyRNN(nn.Module):
    def __init__(self, input_size = 2, hidden_size = 5, output_size = 1):
        super(MyRNN, self).__init__()
        self.hidden_size = hidden_size
        self.in2hidden = nn.Linear(input_size + hidden_size, hidden_size)
        self.in2output = nn.Linear(input_size + hidden_size, output_size)
    
    def forward(self, x, hidden_state):
        combined = torch.cat((x, hidden_state), 1)
        hidden = torch.sigmoid(self.in2hidden(combined))
        output = self.in2output(combined)
        return output, hidden
    
    def init_hidden(self):
        return nn.init.kaiming_uniform_(torch.empty(1, self.hidden_size))

[[1 1]
 [2 2]
 [4 4]
 [3 3]]


In [58]:
rnn = MyRNN()
print(rnn)

MyRNN(
  (in2hidden): Linear(in_features=7, out_features=5, bias=True)
  (in2output): Linear(in_features=7, out_features=1, bias=True)
)


In [69]:
from torch.optim import SGD
from torch.optim.lr_scheduler import ReduceLROnPlateau

optimizer = torch.optim.Adam(rnn.parameters(), lr=0.05)   # optimize all cnn parameters
loss_fn = torch.nn.MSELoss(size_average=False)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=17, gamma = 0.99)

In [72]:
for epoch in range(100):
    for x in range(17):
        hidden_state = rnn.init_hidden() 
        if x == 0:
            dailyInputs = inputs[:int(splitInputs[x])]            
        else:           
            dailyInputs = inputs[int(sum(splitInputs[:x])) :int(sum(splitInputs[:x])) + int(splitInputs[x])]
        for y in range(int(splitInputs[x])):            
            output, hidden_state = rnn(dailyInputs[y].view(1,2), hidden_state)                               # rnn output
       
        loss = loss_fn(output, outputs[x].view(1, 1))                   #  loss
        optimizer.zero_grad()                           # clear gradients for this training step
        loss.backward()                                 # backpropagation, compute gradients
        optimizer.step() 
        scheduler.step()
        # apply gradients
    print(scheduler.get_last_lr())

    print('Epoch: ', epoch, '| train loss: %.4f' % loss.data)



[0.013263987810938228]
Epoch:  0 | train loss: 0.0305
[0.013131347932828845]
Epoch:  1 | train loss: 0.0305
[0.013000034453500557]
Epoch:  2 | train loss: 0.0304
[0.01287003410896555]
Epoch:  3 | train loss: 0.0303
[0.012741333767875895]
Epoch:  4 | train loss: 0.0302
[0.012613920430197136]
Epoch:  5 | train loss: 0.0302
[0.012487781225895164]
Epoch:  6 | train loss: 0.0301
[0.012362903413636212]
Epoch:  7 | train loss: 0.0300
[0.01223927437949985]
Epoch:  8 | train loss: 0.0299
[0.012116881635704851]
Epoch:  9 | train loss: 0.0299
[0.011995712819347802]
Epoch:  10 | train loss: 0.0298
[0.011875755691154323]
Epoch:  11 | train loss: 0.0297
[0.01175699813424278]
Epoch:  12 | train loss: 0.0297
[0.011639428152900352]
Epoch:  13 | train loss: 0.0296
[0.011523033871371349]
Epoch:  14 | train loss: 0.0295
[0.011407803532657634]
Epoch:  15 | train loss: 0.0295
[0.011293725497331058]
Epoch:  16 | train loss: 0.0294
[0.011180788242357747]
Epoch:  17 | train loss: 0.0293
[0.01106898035993417]
E

KeyboardInterrupt: 

In [74]:
for x in range(20):
    hidden_state = rnn.init_hidden()

    if x == 0:
        dailyInputs = inputs[:int(splitInputs[x])]            
    else:           
        dailyInputs = inputs[int(sum(splitInputs[:x])) :int(sum(splitInputs[:x])) + int(splitInputs[x])]
    
    for y in range(int(splitInputs[x])):            
        output, hidden_state = rnn(dailyInputs[y].view(1,2), hidden_state)
    print(output[0][0], " : ", outputs[x][0], 'train loss: %.4f' % loss.data)
    loss = loss_fn(output, outputs[x].view(1, 1))  
    print('train loss: %.4f' % loss.data)

tensor(-0.1512, grad_fn=<SelectBackward0>)  :  tensor(1.) train loss: 0.0004
train loss: 1.3252
tensor(-0.1889, grad_fn=<SelectBackward0>)  :  tensor(0.0290) train loss: 1.3252
train loss: 0.0475
tensor(-0.1411, grad_fn=<SelectBackward0>)  :  tensor(-0.5040) train loss: 0.0475
train loss: 0.1317
tensor(-0.1152, grad_fn=<SelectBackward0>)  :  tensor(0.7010) train loss: 0.1317
train loss: 0.6662
tensor(-0.1337, grad_fn=<SelectBackward0>)  :  tensor(-0.1973) train loss: 0.6662
train loss: 0.0040
tensor(-0.0984, grad_fn=<SelectBackward0>)  :  tensor(-0.9827) train loss: 0.0040
train loss: 0.7819
tensor(-0.2791, grad_fn=<SelectBackward0>)  :  tensor(-1.) train loss: 0.7819
train loss: 0.5197
tensor(-0.1124, grad_fn=<SelectBackward0>)  :  tensor(-0.6141) train loss: 0.5197
train loss: 0.2518
tensor(-0.2974, grad_fn=<SelectBackward0>)  :  tensor(-0.0505) train loss: 0.2518
train loss: 0.0610
tensor(-0.2021, grad_fn=<SelectBackward0>)  :  tensor(0.1671) train loss: 0.0610
train loss: 0.1364
te